In [2]:
import os
import random
import numpy as np
import sys
import torch
import pprint

root = '/'
pprint.pprint(sys.path)

sys.path.append(import_path)
pprint.pprint(sys.path)

"\nimport torch\n\n# 4つのテンソルがあると仮定\n# node_features, edge_features, mask, props\n\n# 保存するテンソルを辞書形式にまとめる\ndata_to_save = {\n    'node_features': node_features,\n    'edge_features': edge_features,\n    'mask': mask,\n    'props': props\n}\n\n# pickleで保存する（torch.saveで保存可能）\ntorch.save(data_to_save, 'qm9_e3data/tensor_data.pkl')\n"

In [ ]:
import os
import sys
import pprint

import_path = root + 'pigvae_all'
sys.path.append(import_path)
pprint.pprint(sys.path)

import_path1 = root + 'pigvae_all/pigvae'
sys.path.append(import_path1)
pprint.pprint(sys.path)

In [3]:
import numpy as np
import torch
from torch.utils.data import Dataset
from torch.utils.data.distributed import DistributedSampler
import random
#import pytorch_lightning as pl
from torch_geometric.data import Data
from torch_geometric.utils import from_networkx
import networkx as nx
from networkx.algorithms.shortest_paths.dense import floyd_warshall_numpy

from networkx.generators.random_graphs import *
from networkx.generators.ego import ego_graph
from networkx.generators.geometric import random_geometric_graph

/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:86: UserWarning: An issue occurred while importing 'torch-scatter'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_scatter/_version_cpu.so: undefined symbol: _ZN5torch3jit17parseSchemaOrNameERKSsb
  warnings.warn(f"An issue occurred while importing 'torch-scatter'. "
/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:97: UserWarning: An issue occurred while importing 'torch-cluster'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_cluster/_version_cpu.so: undefined symbol: _ZN5torch3jit17parseSchemaOrNameERKSsb
  warnings.warn(f"An issue occurred while importing 'torch-cluster'. "
/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:113: UserWarning: An issue occurred while importing 'torch-spline-conv'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_spline_conv/_version_cpu.so: undefined symbol: _ZN

In [4]:
loaded_data = torch.load(root + 'dataset/train_dataset/qm9_e3data/tensor_data.pkl')

# 各テンソルにアクセス
node_features = loaded_data['node_features']
edge_features = loaded_data['edge_features']
mask = loaded_data['mask']
props = loaded_data['props']

In [5]:
import numpy as np
import torch
from torch.utils.data import Dataset
from torch.utils.data.distributed import DistributedSampler
import random
#import pytorch_lightning as pl
from torch_geometric.data import Data
from torch_geometric.utils import from_networkx
import networkx as nx
from networkx.algorithms.shortest_paths.dense import floyd_warshall_numpy

from networkx.generators.random_graphs import *
from networkx.generators.ego import ego_graph
from networkx.generators.geometric import random_geometric_graph

num_node_f = 36
num_edge_f = 6

In [6]:
node_features.shape, edge_features.shape, mask.shape, props.shape

(torch.Size([132480, 29, 36]),
 torch.Size([132480, 29, 29, 8]),
 torch.Size([132480, 29]),
 torch.Size([132480]))

In [7]:
n_train = 50000
n_val = 60000
n_test = 100000

train_dataset = torch.utils.data.TensorDataset(node_features[0:n_train], edge_features[0:n_train], mask[0:n_train], props[0:n_train])
val_dataset = torch.utils.data.TensorDataset(node_features[n_train:n_val], edge_features[n_train:n_val], mask[n_train:n_val], props[n_train:n_val])
test_dataset = torch.utils.data.TensorDataset(node_features[n_val:n_test], edge_features[n_val:n_test], mask[n_val:n_test], props[n_val:n_test])

In [8]:
train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=20, shuffle=True)
val_loader = torch.utils.data.DataLoader(val_dataset, batch_size=20, shuffle=False)
test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=20, shuffle=False)

In [9]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [10]:
hparams = {
    "vae":True,
    "kld_loss_scale":0.01,
    "perm_loss_scale":0.1,
    "property_loss_scale":0.5,
    "num_node_features":num_node_f,
    "num_edge_features":1+num_edge_f+1,
    "emb_dim": 50,
    'graph_encoder_hidden_dim': 256,
    'graph_encoder_k_dim': 64,
    'graph_encoder_v_dim': 64,
    'graph_encoder_num_heads': 16,
    'graph_encoder_ppf_hidden_dim': 512,
    'graph_encoder_num_layers': 16,
    'graph_decoder_hidden_dim': 256,
    'graph_decoder_k_dim': 64,
    'graph_decoder_v_dim': 64,
    'graph_decoder_num_heads': 16,
    'graph_decoder_ppf_hidden_dim': 512,
    'graph_decoder_num_layers': 16,
    "graph_decoder_pos_emb_dim": 64,
    'property_predictor_hidden_dim': 3,
    'num_properties': 1
}

model_load_dir = root + 'save_models/qm9/pig-e3ae_models/'
model_save_dir = root + 'save_models/qm9/pig-beta-e3diffvae_with_trained-ae_models/'

if not os.path.exists(model_save_dir):
    os.makedirs(model_save_dir)

In [11]:
from torch import nn
from torch.nn import Linear, LayerNorm, Dropout
from torch.nn.functional import relu, pad
from pigvae.graph_transformer import Transformer, PositionalEncoding
from pigvae.models import GraphEncoder, GraphDecoder, Permuter
from torch import nn
from torch.nn import Linear, LayerNorm, Dropout
from torch.nn.functional import relu, pad
from pigvae.graph_transformer import Transformer, PositionalEncoding
from pigvae.models import GraphAE

In [12]:
#device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#model0 = GraphAE(hparams).to(device)

In [13]:
#load_model_path = model_load_dir + "pigvae_best_model.pt"
#model0 = torch.load(load_model_path)

In [14]:
"""
save_model_path1 = model_load_dir + "pig_enc" + ".pt"
save_model_path2 = model_load_dir + "pig_dec" + ".pt"
save_model_path3 = model_load_dir + "pig_bn_enc" + ".pt"
save_model_path4 = model_load_dir + "pig_bn_dec" + ".pt"
save_model_path5 = model_load_dir + "pig_prop" + ".pt"
save_model_path6 = model_load_dir + "pig_perm" + ".pt"

torch.save(model0.encoder, save_model_path1)
torch.save(model0.decoder, save_model_path2)
torch.save(model0.bottle_neck_encoder.w, save_model_path3)
torch.save(model0.bottle_neck_decoder, save_model_path4)
torch.save(model0.property_predictor, save_model_path5)
torch.save(model0.permuter, save_model_path6)
"""

'\nsave_model_path1 = model_load_dir + "pig_enc" + ".pt"\nsave_model_path2 = model_load_dir + "pig_dec" + ".pt"\nsave_model_path3 = model_load_dir + "pig_bn_enc" + ".pt"\nsave_model_path4 = model_load_dir + "pig_bn_dec" + ".pt"\nsave_model_path5 = model_load_dir + "pig_prop" + ".pt"\nsave_model_path6 = model_load_dir + "pig_perm" + ".pt"\n\ntorch.save(model0.encoder, save_model_path1)\ntorch.save(model0.decoder, save_model_path2)\ntorch.save(model0.bottle_neck_encoder.w, save_model_path3)\ntorch.save(model0.bottle_neck_decoder, save_model_path4)\ntorch.save(model0.property_predictor, save_model_path5)\ntorch.save(model0.permuter, save_model_path6)\n'

In [15]:
load_model_path1 = model_load_dir + "pig_enc" + ".pt"
load_model_path2 = model_load_dir + "pig_dec" + ".pt"
load_model_path3 = model_load_dir + "pig_bn_enc" + ".pt"
load_model_path4 = model_load_dir + "pig_bn_dec" + ".pt"
load_model_path5 = model_load_dir + "pig_prop" + ".pt"
load_model_path6 = model_load_dir + "pig_perm" + ".pt"

In [16]:
load_ddpm_path = model_load_dir + "ddpm/ddpm_best_model" + ".pt"

## Denoising Model Calss

In [17]:
import os
import torch
import numpy as np
from torch.optim import Adam, lr_scheduler
from ddpm_torch.utils import seed_all, infer_range
from ddpm_torch.toy import *

import torch
import torch.nn as nn

from ddpm_torch.modules import Linear, Sequential
from ddpm_torch.functions import get_timestep_embedding


DEFAULT_NORMALIZER = nn.LayerNorm
DEFAULT_NONLINEARITY = nn.LeakyReLU(negative_slope=0.02, inplace=True)


class TemporalLayer(nn.Module):
    normalize = DEFAULT_NORMALIZER
    nonlinearity = DEFAULT_NONLINEARITY

    def __init__(self, in_features, out_features, temporal_features):
        super(TemporalLayer, self).__init__()
        self.norm1 = self.normalize(in_features)
        self.fc1 = Linear(in_features, out_features, bias=False)
        self.norm2 = self.normalize(out_features)
        self.fc2 = Linear(out_features, out_features, bias=False)
        self.enc = Linear(temporal_features, out_features)

        self.skip = nn.Identity() if in_features == out_features else Linear(in_features, out_features, bias=False)

    def forward(self, x, t_emb):
        out = self.fc1(self.nonlinearity(self.norm1(x)))
        out += self.enc(t_emb)
        out = self.fc2(self.nonlinearity(self.norm2(out)))
        skip = self.skip(x)
        return out + skip


class Denoiser(nn.Module):
    normalize = DEFAULT_NORMALIZER
    nonlinearity = DEFAULT_NONLINEARITY

    def __init__(self, in_features, mid_features, num_temporal_layers):
        super(Denoiser, self).__init__()

        self.in_fc = Linear(in_features, mid_features, bias=False)
        self.temp_fc = Sequential(*([TemporalLayer(
            mid_features, mid_features, mid_features), ] * num_temporal_layers))
        self.out_norm = self.normalize(mid_features)
        self.out_fc = Linear(mid_features, in_features)
        self.t_proj = nn.Sequential(
            Linear(mid_features, mid_features),
            self.nonlinearity)
        self.mid_features = mid_features

    def forward(self, x, t):
        t_emb = get_timestep_embedding(t, self.mid_features)
        t_emb = self.t_proj(t_emb)
        out = self.in_fc(x)
        out = self.temp_fc(out, t_emb=t_emb)
        out = self.out_fc(self.out_norm(out))
        return out

In [18]:
# model parameters
model_mean_type = "eps"
model_var_type = "fixed-large"
loss_type = "mse"
lat_dim = 50
in_features = lat_dim
out_features = 2 * in_features if model_var_type == "learned" else in_features
mid_features = 256
num_temporal_layers = 3

In [19]:
# diffusion parameters
beta_schedule = "linear"
beta_start, beta_end = 0.001, 0.2
timesteps = 500
betas = get_beta_schedule(beta_schedule, beta_start=beta_start, beta_end=beta_end, timesteps=timesteps)

In [20]:
from pigvae.models import GraphEncoder, GraphDecoder, Permuter 
from pigvae.models import BottleNeckEncoder, BottleNeckDecoder, PropertyPredictor

import torch
from torch.nn import Linear, LayerNorm, Dropout
from torch.nn.functional import relu, pad
from pigvae.graph_transformer import Transformer, PositionalEncoding
from pigvae.synthetic_graphs.data import DenseGraphBatch


class GraphLDA(torch.nn.Module):
    def __init__(self, hparams):
        super().__init__()
        self.vae = hparams["vae"]
        self.encoder = GraphEncoder(hparams)
        self.bottle_neck_encoder = BottleNeckEncoder(hparams)
        self.bottle_neck_decoder = BottleNeckDecoder(hparams)
        self.property_predictor = PropertyPredictor(hparams)
        self.permuter = Permuter(hparams)
        self.decoder = GraphDecoder(hparams)

        self.dense_fn = Denoiser(in_features, mid_features, num_temporal_layers)
        self.diffusion = GaussianDiffusion(betas=betas, model_mean_type=model_mean_type, model_var_type=model_var_type, loss_type=loss_type)

    def encode(self, node_features, edge_features, mask):

        graph_emb, node_features = self.encoder(
            node_features=node_features,
            edge_features=edge_features,
            mask=mask,
        )
        graph_emb, mu, logvar = self.bottle_neck_encoder(graph_emb)
        return  graph_emb, mu, logvar, node_features

    def decode(self, graph_emb, perm, mask=None):
        props = self.property_predictor(graph_emb).squeeze()

        """
        if mask is None:
            num_nodes = torch.round(props * STD_NUM_NODES + MEAN_NUM_NODES).long()
            mask = torch.arange(max(num_nodes)).type_as(num_nodes).unsqueeze(0) < num_nodes.unsqueeze(1)
        """
        
        graph_emb = self.bottle_neck_decoder(graph_emb)
        node_logits, edge_logits = self.decoder(
            graph_emb=graph_emb,
            perm=perm,
            mask=mask
        )

        return node_logits, edge_logits, props

    def forward(self, node_features, edge_features, mask, training, tau):
        graph_emb, mu, logvar, node_features = self.encode(node_features, edge_features, mask)
        perm = self.permuter(node_features, mask=mask, hard=not training, tau=tau)

        #diffusion process
        z_0 = graph_emb
        B = z_0.shape[0]
        T = self.diffusion.timesteps
        t = torch.randint(T, size=(B, ), dtype=torch.int64, device=device)
        t_noise = torch.randn_like(graph_emb)
        z_t = self.diffusion.q_sample(z_0, t, noise=t_noise)

        #denoising
        model_out = self.dense_fn(z_t, t) #model_out : 出力, t_noise : 予測するターゲット
        
        #deocde from noisy latent vector
        graph_pred = self.decode(z_0, perm, mask)

        return graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise

class BottleNeckEncoder(torch.nn.Module):
    def __init__(self, hparams):
        super().__init__()
        self.d_in = hparams["graph_encoder_hidden_dim"]
        self.d_out = hparams["emb_dim"]
        self.wu = Linear(self.d_in, self.d_out)
        self.wv = Linear(self.d_in, self.d_out)

    def forward(self, x):
        mu = self.wu(relu(x))
        logvar = self.wv(relu(x))
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        z = mu + eps * std

        return z, mu, logvar

In [21]:
model = GraphLDA(hparams).to(device)

In [22]:
model.encoder = torch.load(load_model_path1)
model.decoder = torch.load(load_model_path2)
model.bottle_neck_encoder.wu = torch.load(load_model_path3)
model.bottle_neck_decoder = torch.load(load_model_path4)
model.property_predictor = torch.load(load_model_path5)
model.permuter = torch.load(load_model_path6)
model.dense_fn = torch.load(load_ddpm_path)

In [23]:
B = 20
grad_norm = 0

In [24]:
from pigvae.synthetic_graphs.critic_qm9 import Critic

critic = Critic(hparams, device)
lr = 0.00005

optimizer = torch.optim.Adam([
    {'params': model.encoder.parameters()},
    {'params': model.decoder.parameters()},
    {'params': model.bottle_neck_encoder.parameters()},
    {'params': model.bottle_neck_decoder.parameters()},
    {'params': model.property_predictor.parameters()},
    {'params': model.permuter.parameters()},
    {'params': model.dense_fn.parameters(), 'lr': 0.0005}
], lr=lr, betas=(0.9, 0.98))

lr_scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer=optimizer, gamma=0.9)

# Training

In [25]:
train_loss_list = []
val_loss_list = []

def val_preds(epoch):
    
    model.eval()
    
    sum_errors = 0
    
    for batch_idx, batch_data in enumerate(val_loader):
       
        with torch.no_grad():
            
            if torch.cuda.is_available():
                node_features, edge_features, mask, props = batch_data
                node_features, edge_features, mask, props = node_features.to(device), edge_features.to(device), mask.to(device), props.to(device)

            graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise = model(node_features, edge_features, mask, training=True, tau=1.0)
            node_logits, edge_logits, pred_props = graph_pred

            vae_loss = critic(node_features, edge_features, props, node_logits, edge_logits, pred_props, mask, perm, mu, logvar)

            batch_vae_loss = vae_loss['node_loss'] * 10 + vae_loss['edge_loss'] * 10 + vae_loss['dist_loss'] * 10 + vae_loss['perm_loss'] * 0.1
            diffusion_loss = torch.sum((t_noise - model_out).pow(2), dim = 1).mean()
            entropy_loss = - torch.mean(torch.sum(logvar,dim=1))
            batch_all_loss = batch_vae_loss + diffusion_loss * beta + entropy_loss * gamma

            if batch_idx % 10 == 0:
                print(vae_loss)
                print("Epoch (val) : ", epoch, "  batch (val) : ", batch_idx , "Loss sum (val) : ", batch_all_loss.data.item(), "dsm (val) : ", diffusion_loss.data.item(), "neg entropy (val) : ", entropy_loss.data.item())
                
            sum_errors = sum_errors + vae_loss['node_loss'].data.item() * 10 + vae_loss['edge_loss'].data.item() * 10 \
             + diffusion_loss.data.item() * beta + entropy_loss.data.item() * gamma + vae_loss['dist_loss'].data.item() * 10

            del batch_all_loss
            torch.cuda.empty_cache()
            
    return sum_errors

In [26]:
import datetime

# テキストファイルのパスを指定
log_path = model_save_dir + 'log.txt'

f = open(log_path, 'w')
f.write('train -- logs')
f.close()

def logging_txt(epoch):
    dt_now = datetime.datetime.now()
    
    # ファイルを読み込んで、末尾の行を取得
    with open(log_path, 'r') as file:
        lines = file.readlines()
        last_line = lines[-1].strip()

    # 末尾の行に追記する文字列を指定
    append_string = "epoch " + str(epoch) + " : " + str(dt_now)

    # ファイルに追記
    with open(log_path, 'a') as file:
        file.write('\n' + append_string)

In [27]:
num_epochs = 100
beta = 0.1
gamma = 1e-4
best_loss = 10000000

for epoch in range(num_epochs):
    model.train()

    sum_errors = 0
    
    for batch_idx, batch_data in enumerate(train_loader):

        node_features, edge_features, mask, props = batch_data
        node_features, edge_features, mask, props = node_features.to(device), edge_features.to(device), mask.to(device), props.to(device)
    
        optimizer.zero_grad()

        graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise = model(node_features, edge_features, mask, training=True, tau=1.0)
        node_logits, edge_logits, pred_props = graph_pred

        vae_loss = critic(node_features, edge_features, props, node_logits, edge_logits, pred_props, mask, perm, mu, logvar)

        batch_vae_loss = vae_loss['node_loss'] * 10 + vae_loss['edge_loss'] * 10 + vae_loss['dist_loss'] * 10 + vae_loss['perm_loss'] * 0.1
        diffusion_loss = torch.sum((t_noise - model_out).pow(2), dim = 1).mean()
        entropy_loss = - torch.mean(torch.sum(logvar,dim=1))
        batch_all_loss = batch_vae_loss + diffusion_loss * beta + entropy_loss * gamma

        if batch_idx % 100 == 0:
            print("Epoch : ", epoch, " Batch : ", batch_idx, " Loss : ", batch_all_loss.data.item(), "dsm : ", diffusion_loss.data.item(), "neg entropy : ", entropy_loss.data.item())
            print(vae_loss)
        
        sum_errors = sum_errors + vae_loss['node_loss'].data.item() * 10 + vae_loss['edge_loss'].data.item() * 10 \
         + diffusion_loss.data.item() * beta + entropy_loss.data.item() * gamma + vae_loss['dist_loss'].data.item() * 10

        batch_all_loss.backward()

        optimizer.step()

        del batch_all_loss
        torch.cuda.empty_cache()
    
    lr_scheduler.step()
    
    train_loss_list.append(sum_errors / len(train_loader))
    val_loss = val_preds(epoch) / len(val_loader)
    val_loss_list.append(val_loss)

    np.save(model_save_dir + "train_loss_hist", np.array(train_loss_list))
    np.save(model_save_dir + "val_loss_hist", np.array(val_loss_list))
    
    logging_txt(epoch)

    if val_loss < best_loss:
        save_model_path = model_save_dir + "pigvae_best_model" + ".pt"
        torch.save(model, save_model_path)

        optimizer_path = model_save_dir + "opt_best_model" + ".pt"
        torch.save(optimizer.state_dict(), optimizer_path)
        
        best_loss = val_loss

Epoch :  0  Batch :  0  Loss :  19.16120147705078 dsm :  5.522905349731445 neg entropy :  1.7637596130371094
{'edge_loss': tensor(0.3418, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(1.2992, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.2024, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(2.8714, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.7486, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(303.8594, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  10  Loss :  9.775337219238281 dsm :  4.001579284667969 neg entropy :  6.939844608306885
{'edge_loss': tensor(0.1783, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.6443, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0968, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(3.4541, device='cuda:0', grad_fn=<MeanBackward0>)

Epoch :  0  Batch :  150  Loss :  4.759096622467041 dsm :  1.6533336639404297 neg entropy :  36.75525665283203
{'edge_loss': tensor(0.1038, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.2942, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0431, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(10.5390, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.8309, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(320.1051, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  160  Loss :  6.220527648925781 dsm :  4.060079097747803 neg entropy :  36.26021957397461
{'edge_loss': tensor(0.1295, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.3767, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0565, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(11.8636, device='cuda:0', grad_fn=<MeanBackwa

Epoch :  0  Batch :  300  Loss :  8.773472785949707 dsm :  6.72552490234375 neg entropy :  55.92698287963867
{'edge_loss': tensor(0.1962, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.5096, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0846, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(18.1657, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.9734, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(308.6089, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  310  Loss :  8.41476821899414 dsm :  1.5007869005203247 neg entropy :  55.187530517578125
{'edge_loss': tensor(0.1947, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.5287, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0856, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(19.2700, device='cuda:0', grad_fn=<MeanBackwar

Epoch :  0  Batch :  450  Loss :  3.7049570083618164 dsm :  3.20658802986145 neg entropy :  81.55229949951172
{'edge_loss': tensor(0.0768, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.2091, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0353, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(26.9523, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.7241, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(296.2940, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  460  Loss :  4.734844207763672 dsm :  2.997469425201416 neg entropy :  82.59001922607422
{'edge_loss': tensor(0.0866, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.3077, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0301, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(27.2734, device='cuda:0', grad_fn=<MeanBackwar

Epoch :  0  Batch :  600  Loss :  4.776431083679199 dsm :  8.346250534057617 neg entropy :  104.1522445678711
{'edge_loss': tensor(0.0973, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.2446, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0345, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(36.1890, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.7789, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(297.8426, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  610  Loss :  4.6388349533081055 dsm :  7.316648960113525 neg entropy :  104.89250946044922
{'edge_loss': tensor(0.0935, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.2436, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0355, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(36.9304, device='cuda:0', grad_fn=<MeanBackw

...

Epoch :  99  Batch :  2180  Loss :  1.4071109294891357 dsm :  1.528383493423462 neg entropy :  609.876953125
{'edge_loss': tensor(0.0405, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.1022, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(-0.0330, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(280.1235, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.5638, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(308.8442, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  99  Batch :  2190  Loss :  1.4451853036880493 dsm :  0.2397030144929886 neg entropy :  607.6920166015625
{'edge_loss': tensor(0.0312, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.1032, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(-0.0083, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(279.0379, device='cuda:0', grad_fn=<Mean

Epoch :  99  Batch :  2330  Loss :  1.7643520832061768 dsm :  0.06859572976827621 neg entropy :  608.5072021484375
{'edge_loss': tensor(0.0402, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.1063, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0137, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(279.4494, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.5413, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(300.5494, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  99  Batch :  2340  Loss :  1.998894453048706 dsm :  0.3546585738658905 neg entropy :  607.9105834960938
{'edge_loss': tensor(0.0504, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.1609, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(-0.0314, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(279.1651, device='cuda:0', grad_fn=<

Epoch :  99  Batch :  2480  Loss :  1.8062864542007446 dsm :  0.861231803894043 neg entropy :  605.2626342773438
{'edge_loss': tensor(0.0360, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.1084, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(0.0114, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(277.8081, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.6121, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(319.1758, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  99  Batch :  2490  Loss :  1.0332595109939575 dsm :  0.08847098797559738 neg entropy :  608.5679321289062
{'edge_loss': tensor(0.0369, device='cuda:0', grad_fn=<DivBackward0>), 'dist_loss': tensor(0.0928, device='cuda:0', grad_fn=<MseLossBackward0>), 'node_loss': tensor(-0.0417, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(279.4761, device='cuda:0', grad_fn=<

{'edge_loss': tensor(0.0299, device='cuda:0'), 'dist_loss': tensor(0.1081, device='cuda:0'), 'node_loss': tensor(-0.0277, device='cuda:0'), 'kld_loss': tensor(290.9635, device='cuda:0'), 'perm_loss': tensor(1.7183, device='cuda:0'), 'property_loss': tensor(346.5764, device='cuda:0')}
Epoch (val) :  99   batch (val) :  170 Loss sum (val) :  1.291478157043457 dsm (val) :  0.15705813467502594 neg entropy (val) :  631.53564453125
{'edge_loss': tensor(0.0279, device='cuda:0'), 'dist_loss': tensor(0.0877, device='cuda:0'), 'node_loss': tensor(-0.0410, device='cuda:0'), 'kld_loss': tensor(291.1130, device='cuda:0'), 'perm_loss': tensor(1.5851, device='cuda:0'), 'property_loss': tensor(325.7505, device='cuda:0')}
Epoch (val) :  99   batch (val) :  180 Loss sum (val) :  0.9076583385467529 dsm (val) :  0.018043212592601776 neg entropy (val) :  631.8508911132812
{'edge_loss': tensor(0.0423, device='cuda:0'), 'dist_loss': tensor(0.1727, device='cuda:0'), 'node_loss': tensor(-0.0062, device='cuda:0

{'edge_loss': tensor(0.0269, device='cuda:0'), 'dist_loss': tensor(0.0640, device='cuda:0'), 'node_loss': tensor(-0.0177, device='cuda:0'), 'kld_loss': tensor(290.9272, device='cuda:0'), 'perm_loss': tensor(1.5762, device='cuda:0'), 'property_loss': tensor(320.3940, device='cuda:0')}
Epoch (val) :  99   batch (val) :  360 Loss sum (val) :  0.8996366262435913 dsm (val) :  0.08689180761575699 neg entropy (val) :  631.45654296875
{'edge_loss': tensor(0.0373, device='cuda:0'), 'dist_loss': tensor(0.1044, device='cuda:0'), 'node_loss': tensor(-0.0213, device='cuda:0'), 'kld_loss': tensor(290.4718, device='cuda:0'), 'perm_loss': tensor(1.4305, device='cuda:0'), 'property_loss': tensor(278.8233, device='cuda:0')}
Epoch (val) :  99   batch (val) :  370 Loss sum (val) :  1.3619821071624756 dsm (val) :  0.14793720841407776 neg entropy (val) :  630.578369140625
{'edge_loss': tensor(0.0286, device='cuda:0'), 'dist_loss': tensor(0.0885, device='cuda:0'), 'node_loss': tensor(-0.0218, device='cuda:0'